In [119]:
import os, json, re    

In [120]:
def importJSONFiles(files: list, path: str) -> list[dict[str, any]]:

    hts_data = []

    for file in files:

        with open(f'{path}/{file}') as f:
            header = re.sub(r'\.json', '', file)
            hts_data.append(
                {
                    'header': header,
                    'data': json.loads(f.read())
                })

    return hts_data

def getHTSRecord(hts_data: list[dict[str, any]], queryStr: str):

    for record in hts_data:
        
        if record['header'] == queryStr:
            return record['data']
    
    return 'No record found'

In [121]:
def navigateIndents(currentIndent: int, index_navigation: int, hts_record: list[dict[str, any]]):

    result = []

    for i in range(index_navigation-1, 0, -1):

        if hts_record[i]['indent'] < currentIndent and 'htsno' not in hts_record[i]:
            
            result.append({
                'EH': True,
                'data': hts_record[i]
            })
        
        elif hts_record[i]['indent'] >= currentIndent and 'htsno' in hts_record[i]:
            return result
        
    return result

In [122]:
def queryNavigation(hts_record: list[dict[str, any]], query: list[str]) -> list[dict[str, any]]:

    result = []
    index_query = 1
    index_navigation = 0

    while index_query < len(query):

        index_navigation = 0
        EH_records = []
        for rec in hts_record:

            if 'htsno' in rec and re.match(rf'{query[index_query]}$', rec['htsno']):
                
                EH_records = navigateIndents(rec['indent'], index_navigation, hts_record)
                if EH_records:
                    result.extend(EH_records)
                result.append(rec)

            index_navigation += 1
            
        index_query += 1
    
    return result

In [123]:
path = '../../db_hts/temp/NEW_final_json_files'
query = ["0201", "0201.20", "0201.20.06", "0201.20.06.00"]
files = os.listdir(path)
hts_data = importJSONFiles(files, path)
hts_data

[{'header': '0101',
  'data': [{'htsno': '0101',
    'indent': 0,
    'description': 'Live horses, asses, mules and hinnies:'},
   {'indent': 1, 'description': 'Horses:', 'superior': 'true'},
   {'htsno': '0101.21.00',
    'indent': 2,
    'description': 'Purebred breeding animals',
    'general': 'Free',
    'other': 'Free',
    'footnotes': [{'columns': ['general'],
      'marker': '1',
      'value': 'See 9903.88.15. ',
      'type': 'endnote'}]},
   {'htsno': '0101.21.00.10',
    'indent': 3,
    'description': 'Males',
    'units': ['No.']},
   {'htsno': '0101.21.00.20',
    'indent': 3,
    'description': 'Females',
    'units': ['No.']},
   {'htsno': '0101.29.00',
    'indent': 2,
    'description': 'Other',
    'general': 'Free',
    'other': '20%',
    'footnotes': [{'columns': ['general'],
      'marker': '1',
      'value': 'See 9903.88.15. ',
      'type': 'endnote'}]},
   {'htsno': '0101.29.00.10',
    'indent': 3,
    'description': 'Imported for immediate slaughter',
   

In [124]:
hts_record = getHTSRecord(hts_data, query[0])
hts_record

[{'htsno': '0201',
  'indent': 0,
  'description': 'Meat of bovine animals, fresh or chilled:'},
 {'htsno': '0201.10',
  'indent': 1,
  'description': 'Carcasses and half-carcasses:'},
 {'htsno': '0201.10.05',
  'indent': 2,
  'description': 'Described in general note 15 of the tariff schedule and entered pursuant to its provisions',
  'general': '4.4¢/kg',
  'special': 'Free (A+,AU,BH,CL,CO,D,E*, IL,JO,KR,MA,OM,P,PA,PE,S, SG)',
  'other': '13.2¢/kg',
  'footnotes': [{'columns': ['general'],
    'marker': '1',
    'value': 'See 9903.88.15. ',
    'type': 'endnote'}]},
 {'htsno': '0201.10.05.10',
  'indent': 3,
  'description': 'Veal',
  'units': ['kg']},
 {'htsno': '0201.10.05.90',
  'indent': 3,
  'description': 'Other',
  'units': ['kg']},
 {'htsno': '0201.10.10',
  'indent': 2,
  'description': 'Described in additional U.S. note 3 to this chapter and entered pursuant to its provisions',
  'general': '4.4¢/kg',
  'special': 'Free (A+,AU,BH,CL,CO,D,E*,IL,JO,KR,MA,OM,P,PA,PE,S,SG)',
  

In [125]:
result = queryNavigation(hts_record, query)
result

[{'htsno': '0201.20', 'indent': 1, 'description': 'Other cuts with bone in:'},
 {'htsno': '0201.20.06.00',
  'indent': 3,
  'description': 'Other',
  'units': ['kg'],
  'general': '4.4¢/kg',
  'special': 'Free (A+,AU,BH,CL,CO,D,E*, IL,JO,KR,MA,OM,P,PA, PE,S,SG)',
  'other': '13.2¢/kg',
  'footnotes': [{'columns': ['general'],
    'marker': '1',
    'value': 'See 9903.88.15. ',
    'type': 'endnote'}]}]